# Batch Normalization
One way to make deep networks easier to train is to use more sophisticated optimization procedures such as SGD+momentum, RMSProp, or Adam. Another strategy is to change the architecture of the network to make it easier to train. 
One idea along these lines is batch normalization which was proposed by [1] in 2015.

The idea is relatively straightforward. Machine learning methods tend to work better when their input data consists of uncorrelated features with zero mean and unit variance. When training a neural network, we can preprocess the data before feeding it to the network to explicitly decorrelate its features; this will ensure that the first layer of the network sees data that follows a nice distribution. However, even if we preprocess the input data, the activations at deeper layers of the network will likely no longer be decorrelated and will no longer have zero mean or unit variance since they are output from earlier layers in the network. Even worse, during the training process the distribution of features at each layer of the network will shift as the weights of each layer are updated.

The authors of [1] hypothesize that the shifting distribution of features inside deep neural networks may make training deep networks more difficult. To overcome this problem, [1] proposes to insert batch normalization layers into the network. At training time, a batch normalization layer uses a minibatch of data to estimate the mean and standard deviation of each feature. These estimated means and standard deviations are then used to center and normalize the features of the minibatch. A running average of these means and standard deviations is kept during training, and at test time these running averages are used to center and normalize features.

It is possible that this normalization strategy could reduce the representational power of the network, since it may sometimes be optimal for certain layers to have features that are not zero-mean or unit variance. To this end, the batch normalization layer includes learnable shift and scale parameters for each feature dimension.

[1] [Sergey Ioffe and Christian Szegedy, "Batch Normalization: Accelerating Deep Network Training by Reducing
Internal Covariate Shift", ICML 2015.](https://arxiv.org/abs/1502.03167)

In [1]:
# As usual, a bit of setup
import time
import numpy as np
import matplotlib.pyplot as plt
from cs231n.classifiers.fc_net import *
from cs231n.data_utils import get_CIFAR10_data
from cs231n.gradient_check import eval_numerical_gradient, eval_numerical_gradient_array
from cs231n.solver import Solver

%matplotlib inline
plt.rcParams['figure.figsize'] = (10.0, 8.0) # set default size of plots
plt.rcParams['image.interpolation'] = 'nearest'
plt.rcParams['image.cmap'] = 'gray'

# for auto-reloading external modules
# see http://stackoverflow.com/questions/1907993/autoreload-of-modules-in-ipython
%load_ext autoreload
%autoreload 2

def rel_error(x, y):
    """ returns relative error """
    return np.max(np.abs(x - y) / (np.maximum(1e-8, np.abs(x) + np.abs(y))))

def print_mean_std(x,axis=0):
    print('  means: ', x.mean(axis=axis))
    print('  stds:  ', x.std(axis=axis))
    print() 

In [2]:
# Load the (preprocessed) CIFAR10 data.
data = get_CIFAR10_data()
for k, v in data.items():
  print('%s: ' % k, v.shape)

X_train:  (49000, 3, 32, 32)
y_train:  (49000,)
X_val:  (1000, 3, 32, 32)
y_val:  (1000,)
X_test:  (1000, 3, 32, 32)
y_test:  (1000,)


## Batch normalization: forward
In the file `cs231n/layers.py`, implement the batch normalization forward pass in the function `batchnorm_forward`. Once you have done so, run the following to test your implementation.

Referencing the paper linked to above in [1] may be helpful!

In [3]:
# Check the training-time forward pass by checking means and variances
# of features both before and after batch normalization   

# Simulate the forward pass for a two-layer network
np.random.seed(231)
N, D1, D2, D3 = 200, 50, 60, 3
X = np.random.randn(N, D1)
W1 = np.random.randn(D1, D2)
W2 = np.random.randn(D2, D3)
a = np.maximum(0, X.dot(W1)).dot(W2)

print('Before batch normalization:')
print_mean_std(a,axis=0)

gamma = np.ones((D3,))
beta = np.zeros((D3,))
# Means should be close to zero and stds close to one
print('After batch normalization (gamma=1, beta=0)')
a_norm, _ = batchnorm_forward(a, gamma, beta, {'mode': 'train'})
print_mean_std(a_norm,axis=0)

gamma = np.asarray([1.0, 2.0, 3.0])
beta = np.asarray([11.0, 12.0, 13.0])
# Now means should be close to beta and stds close to gamma
print('After batch normalization (gamma=', gamma, ', beta=', beta, ')')
a_norm, _ = batchnorm_forward(a, gamma, beta, {'mode': 'train'})
print_mean_std(a_norm,axis=0)

Before batch normalization:
  means:  [ -2.3814598  -13.18038246   1.91780462]
  stds:   [27.18502186 34.21455511 37.68611762]

After batch normalization (gamma=1, beta=0)
  means:  [5.32907052e-17 7.04991621e-17 4.22578639e-17]
  stds:   [0.99999999 1.         1.        ]

After batch normalization (gamma= [1. 2. 3.] , beta= [11. 12. 13.] )
  means:  [11. 12. 13.]
  stds:   [0.99999999 1.99999999 2.99999999]



In [4]:
# Check the test-time forward pass by running the training-time
# forward pass many times to warm up the running averages, and then
# checking the means and variances of activations after a test-time
# forward pass.

np.random.seed(231)
N, D1, D2, D3 = 200, 50, 60, 3
W1 = np.random.randn(D1, D2)
W2 = np.random.randn(D2, D3)

bn_param = {'mode': 'train'}
gamma = np.ones(D3)
beta = np.zeros(D3)

for t in range(50):
  X = np.random.randn(N, D1)
  a = np.maximum(0, X.dot(W1)).dot(W2)
  batchnorm_forward(a, gamma, beta, bn_param)

bn_param['mode'] = 'test'
X = np.random.randn(N, D1)
a = np.maximum(0, X.dot(W1)).dot(W2)
a_norm, _ = batchnorm_forward(a, gamma, beta, bn_param)

# Means should be close to zero and stds close to one, but will be
# noisier than training-time forward passes.
print('After batch normalization (test-time):')
print_mean_std(a_norm,axis=0)

After batch normalization (test-time):
  means:  [-0.03927354 -0.04349152 -0.10452688]
  stds:   [1.01531428 1.01238373 0.97819988]



## Batch normalization: backward
Now implement the backward pass for batch normalization in the function `batchnorm_backward`.

To derive the backward pass you should write out the computation graph for batch normalization and backprop through each of the intermediate nodes. Some intermediates may have multiple outgoing branches; make sure to sum gradients across these branches in the backward pass.

Once you have finished, run the following to numerically check your backward pass.

In [5]:
# Gradient check batchnorm backward pass
np.random.seed(231)
N, D = 4, 5
x = 5 * np.random.randn(N, D) + 12
gamma = np.random.randn(D)
beta = np.random.randn(D)
dout = np.random.randn(N, D)

bn_param = {'mode': 'train'}
fx = lambda x: batchnorm_forward(x, gamma, beta, bn_param)[0]
fg = lambda a: batchnorm_forward(x, a, beta, bn_param)[0]
fb = lambda b: batchnorm_forward(x, gamma, b, bn_param)[0]

dx_num = eval_numerical_gradient_array(fx, x, dout)
da_num = eval_numerical_gradient_array(fg, gamma.copy(), dout)
db_num = eval_numerical_gradient_array(fb, beta.copy(), dout)

_, cache = batchnorm_forward(x, gamma, beta, bn_param)
dx, dgamma, dbeta = batchnorm_backward(dout, cache)
#You should expect to see relative errors between 1e-13 and 1e-8
print('dx error: ', rel_error(dx_num, dx))
print('dgamma error: ', rel_error(da_num, dgamma))
print('dbeta error: ', rel_error(db_num, dbeta))

dx error:  1.7029261167605239e-09
dgamma error:  7.420414216247087e-13
dbeta error:  2.8795057655839487e-12


## Batch normalization: alternative backward
In class we talked about two different implementations for the sigmoid backward pass. One strategy is to write out a computation graph composed of simple operations and backprop through all intermediate values. Another strategy is to work out the derivatives on paper. For example, you can derive a very simple formula for the sigmoid function's backward pass by simplifying gradients on paper.

Surprisingly, it turns out that you can do a similar simplification for the batch normalization backward pass too!  

In the forward pass, given a set of inputs $X=\begin{bmatrix}x_1\\x_2\\...\\x_N\end{bmatrix}$, 

we first calculate the mean $\mu$ and variance $v$.
With $\mu$ and $v$ calculated, we can calculate the standard deviation $\sigma$  and normalized data $Y$.
The equations and graph illustration below describe the computation ($y_i$ is the i-th element of the vector $Y$).

\begin{align}
& \mu=\frac{1}{N}\sum_{k=1}^N x_k  &  v=\frac{1}{N}\sum_{k=1}^N (x_k-\mu)^2 \\
& \sigma=\sqrt{v+\epsilon}         &  y_i=\frac{x_i-\mu}{\sigma}
\end{align}

<img src="notebook_images/batchnorm_graph.png" width=691 height=202>

The meat of our problem during backpropagation is to compute $\frac{\partial L}{\partial X}$, given the upstream gradient we receive, $\frac{\partial L}{\partial Y}.$ To do this, recall the chain rule in calculus gives us $\frac{\partial L}{\partial X} = \frac{\partial L}{\partial Y} \cdot \frac{\partial Y}{\partial X}$.

The unknown/hart part is $\frac{\partial Y}{\partial X}$. We can find this by first deriving step-by-step our local gradients at 
$\frac{\partial v}{\partial X}$, $\frac{\partial \mu}{\partial X}$,
$\frac{\partial \sigma}{\partial v}$, 
$\frac{\partial Y}{\partial \sigma}$, and $\frac{\partial Y}{\partial \mu}$,
and then use the chain rule to compose these gradients (which appear in the form of vectors!) appropriately to compute $\frac{\partial Y}{\partial X}$.

If it's challenging to directly reason about the gradients over $X$ and $Y$ which require matrix multiplication, try reasoning about the gradients in terms of individual elements $x_i$ and $y_i$ first: in that case, you will need to come up with the derivations for $\frac{\partial L}{\partial x_i}$, by relying on the Chain Rule to first calculate the intermediate $\frac{\partial \mu}{\partial x_i}, \frac{\partial v}{\partial x_i}, \frac{\partial \sigma}{\partial x_i},$ then assemble these pieces to calculate $\frac{\partial y_i}{\partial x_i}$. 

You should make sure each of the intermediary gradient derivations are all as simplified as possible, for ease of implementation. 

After doing so, implement the simplified batch normalization backward pass in the function `batchnorm_backward_alt` and compare the two implementations by running the following. Your two implementations should compute nearly identical results, but the alternative implementation should be a bit faster.

In [22]:
np.random.seed(231)
N, D = 100, 500
x = 5 * np.random.randn(N, D) + 12
gamma = np.random.randn(D)
beta = np.random.randn(D)
dout = np.random.randn(N, D)

bn_param = {'mode': 'train'}
out, cache = batchnorm_forward(x, gamma, beta, bn_param)

t1 = time.time()
dx1, dgamma1, dbeta1 = batchnorm_backward(dout, cache)
t2 = time.time()
dx2, dgamma2, dbeta2 = batchnorm_backward_alt(dout, cache)
t3 = time.time()

print('dx difference: ', rel_error(dx1, dx2))
print('dgamma difference: ', rel_error(dgamma1, dgamma2))
print('dbeta difference: ', rel_error(dbeta1, dbeta2))
print('speedup: %.2fx' % ((t2 - t1) / (t3 - t2)))

dx:  [[-0.00765401 -0.01016893  0.41848192 ...  0.00492498  0.28879534
  -0.08389807]
 [ 0.04910838  0.00381618  0.26077407 ... -0.01484266 -0.28044265
   0.02378907]
 [-0.03733823 -0.00680957 -0.0022472  ... -0.0297766   0.04639493
  -0.13772733]
 ...
 [-0.15302429 -0.02768208 -0.05301902 ... -0.00695181  0.28033542
  -0.05586366]
 [ 0.04619731  0.01273406 -0.18512206 ... -0.00439755  0.30580905
   0.09883873]
 [-0.05143779 -0.0325986  -0.11798756 ...  0.01304426 -0.51769282
  -0.09072919]]
dx_alt:  [[ 0.00249208  0.00080313  0.38891409 ...  0.00202449  0.28339389
  -0.06801918]
 [ 0.05986216  0.01467196  0.27331002 ... -0.01715737 -0.28850312
   0.0381608 ]
 [-0.03371575  0.00905766  0.02542863 ... -0.03190153  0.04564071
  -0.10677975]
 ...
 [-0.16024088 -0.01893715 -0.07442164 ... -0.00941668  0.27695361
  -0.05770829]
 [ 0.04735927  0.0186609  -0.17161848 ... -0.00745667  0.29568049
   0.12872553]
 [-0.02987791 -0.02825927 -0.06514075 ...  0.0104197  -0.52021395
  -0.06847623]]
dx

## Fully Connected Nets with Batch Normalization
Now that you have a working implementation for batch normalization, go back to your `FullyConnectedNet` in the file `cs231n/classifiers/fc_net.py`. Modify your implementation to add batch normalization.

Concretely, when the `normalization` flag is set to `"batchnorm"` in the constructor, you should insert a batch normalization layer before each ReLU nonlinearity. The outputs from the last layer of the network should not be normalized. Once you are done, run the following to gradient-check your implementation.

HINT: You might find it useful to define an additional helper layer similar to those in the file `cs231n/layer_utils.py`. If you decide to do so, do it in the file `cs231n/classifiers/fc_net.py`.

In [14]:
np.random.seed(231)
N, D, H1, H2, C = 2, 15, 20, 30, 10
X = np.random.randn(N, D)
y = np.random.randint(C, size=(N,))

# You should expect losses between 1e-4~1e-10 for W, 
# losses between 1e-08~1e-10 for b,
# and losses between 1e-08~1e-09 for beta and gammas.
for reg in [0, 3.14]:
  print('Running check with reg = ', reg)
  model = FullyConnectedNet([H1, H2], input_dim=D, num_classes=C,
                            reg=reg, weight_scale=5e-2, dtype=np.float64,
                            normalization='batchnorm')

  loss, grads = model.loss(X, y)
  print('Initial loss: ', loss)

  for name in sorted(grads):
    f = lambda _: model.loss(X, y)[0]
    grad_num = eval_numerical_gradient(f, model.params[name], verbose=False, h=1e-5)
    print('%s relative error: %.2e' % (name, rel_error(grad_num, grads[name])))
  if reg == 0: print()

Running check with reg =  0
[[ 4.51510010e-03  3.29563204e-03  2.03327958e-03 -7.63838373e-05
   1.57136236e-04  4.05014451e-05 -9.46162179e-05 -1.21846949e-03
  -5.14618271e-04  2.70765721e-01  6.07256752e-06 -2.28385443e-05
   5.17050549e-06 -1.29335166e-05  2.34802682e-01  2.52673591e-04
  -3.09575626e-04 -9.37398484e-03  9.99021126e-05 -3.21051682e-05
  -4.55510000e-04  1.15662766e-04 -1.31657764e-04 -1.16340114e-01
  -5.67191221e-04 -1.76481864e-05 -8.98646270e-05  6.92276911e-05
  -4.24607098e-04 -3.56819007e-05]
 [-4.51510010e-03 -3.29563204e-03 -2.03327958e-03  7.63838373e-05
  -1.57136236e-04 -4.05014451e-05  9.46162179e-05  1.21846949e-03
   5.14618271e-04 -2.70765721e-01 -6.07256752e-06  2.28385443e-05
  -5.17050549e-06  1.29335166e-05 -2.34802682e-01 -2.52673591e-04
   3.09575626e-04  9.37398484e-03 -9.99021126e-05  3.21051682e-05
   4.55510000e-04 -1.15662766e-04  1.31657764e-04  1.16340114e-01
   5.67191221e-04  1.76481864e-05  8.98646270e-05 -6.92276911e-05
   4.24607098

  -1.45469467e-04 -2.29203650e+00 -6.23447354e-04  6.59300320e-05]]
[[ 4.51510230e-03  3.29563151e-03  2.03328023e-03 -7.63838342e-05
   1.57136235e-04  4.05014428e-05 -9.46162186e-05 -1.21846895e-03
  -5.14618380e-04  2.70765869e-01  6.07256804e-06 -2.28385474e-05
   5.17050570e-06 -1.29335163e-05  2.34802841e-01  2.52673554e-04
  -3.09575746e-04 -9.37396533e-03  9.99020802e-05 -3.21051631e-05
  -4.55509990e-04  1.15662781e-04 -1.31657773e-04 -1.16340152e-01
  -5.67191524e-04 -1.76481885e-05 -8.98646037e-05  6.92276910e-05
  -4.24607114e-04 -3.56819060e-05]
 [-4.51510230e-03 -3.29563151e-03 -2.03328023e-03  7.63838342e-05
  -1.57136235e-04 -4.05014428e-05  9.46162186e-05  1.21846895e-03
   5.14618380e-04 -2.70765869e-01 -6.07256804e-06  2.28385474e-05
  -5.17050570e-06  1.29335163e-05 -2.34802841e-01 -2.52673554e-04
   3.09575746e-04  9.37396533e-03 -9.99020802e-05  3.21051631e-05
   4.55509990e-04 -1.15662781e-04  1.31657773e-04  1.16340152e-01
   5.67191524e-04  1.76481885e-05  8.98

  -1.45469528e-04 -2.29203792e+00 -6.23447802e-04  6.59300799e-05]]
[[ 4.51510010e-03  3.29563204e-03  2.03327958e-03 -7.63838373e-05
   1.57136235e-04  4.05014451e-05 -9.46162179e-05 -1.21846949e-03
  -5.14618271e-04  2.70765720e-01  6.07256752e-06 -2.28385443e-05
   5.17050549e-06 -1.29335166e-05  2.34802680e-01  2.52673591e-04
  -3.09575626e-04 -9.37398484e-03  9.99021126e-05 -3.21051682e-05
  -4.55510000e-04  1.15662766e-04 -1.31657764e-04 -1.16340114e-01
  -5.67191221e-04 -1.76481864e-05 -8.98646270e-05  6.92276911e-05
  -4.24607098e-04 -3.56819007e-05]
 [-4.51510010e-03 -3.29563204e-03 -2.03327958e-03  7.63838373e-05
  -1.57136235e-04 -4.05014451e-05  9.46162179e-05  1.21846949e-03
   5.14618271e-04 -2.70765720e-01 -6.07256752e-06  2.28385443e-05
  -5.17050549e-06  1.29335166e-05 -2.34802680e-01 -2.52673591e-04
   3.09575626e-04  9.37398484e-03 -9.99021126e-05  3.21051682e-05
   4.55510000e-04 -1.15662766e-04  1.31657764e-04  1.16340114e-01
   5.67191221e-04  1.76481864e-05  8.98

  -1.45469530e-04 -2.29203794e+00 -6.23447809e-04  6.59300812e-05]]
[[ 4.51510017e-03  3.29563202e-03  2.03327957e-03 -7.63838375e-05
   1.57136235e-04  4.05014451e-05 -9.46162182e-05 -1.21846947e-03
  -5.14618274e-04  2.70765701e-01  6.07256751e-06 -2.28385442e-05
   5.17050547e-06 -1.29335166e-05  2.34802677e-01  2.52673590e-04
  -3.09575624e-04 -9.37398474e-03  9.99021128e-05 -3.21051682e-05
  -4.55509998e-04  1.15662766e-04 -1.31657762e-04 -1.16340109e-01
  -5.67191213e-04 -1.76481863e-05 -8.98646269e-05  6.92276911e-05
  -4.24607094e-04 -3.56819007e-05]
 [-4.51510017e-03 -3.29563202e-03 -2.03327957e-03  7.63838375e-05
  -1.57136235e-04 -4.05014451e-05  9.46162182e-05  1.21846947e-03
   5.14618274e-04 -2.70765701e-01 -6.07256751e-06  2.28385442e-05
  -5.17050547e-06  1.29335166e-05 -2.34802677e-01 -2.52673590e-04
   3.09575624e-04  9.37398474e-03 -9.99021128e-05  3.21051682e-05
   4.55509998e-04 -1.15662766e-04  1.31657762e-04  1.16340109e-01
   5.67191213e-04  1.76481863e-05  8.98

  -1.45469552e-04 -2.29203794e+00 -6.23447789e-04  6.59300795e-05]]
[[ 4.51510745e-03  3.29563544e-03  2.03327779e-03 -7.63838556e-05
   1.57136245e-04  4.05014500e-05 -9.46162741e-05 -1.21847079e-03
  -5.14618264e-04  2.70765529e-01  6.07256829e-06 -2.28385366e-05
   5.17050748e-06 -1.29335184e-05  2.34802173e-01  2.52673511e-04
  -3.09575573e-04 -9.37399267e-03  9.99020972e-05 -3.21051575e-05
  -4.55510186e-04  1.15662814e-04 -1.31657836e-04 -1.16340260e-01
  -5.67191222e-04 -1.76481805e-05 -8.98646021e-05  6.92277116e-05
  -4.24606973e-04 -3.56818927e-05]
 [-4.51510745e-03 -3.29563544e-03 -2.03327779e-03  7.63838556e-05
  -1.57136245e-04 -4.05014500e-05  9.46162741e-05  1.21847079e-03
   5.14618264e-04 -2.70765529e-01 -6.07256829e-06  2.28385366e-05
  -5.17050748e-06  1.29335184e-05 -2.34802173e-01 -2.52673511e-04
   3.09575573e-04  9.37399267e-03 -9.99020972e-05  3.21051575e-05
   4.55510186e-04 -1.15662814e-04  1.31657836e-04  1.16340260e-01
   5.67191222e-04  1.76481805e-05  8.98

...

  -3.65840598e-05  7.76249518e-06]]
[[ 3.47241474e-03 -2.34064041e-05 -1.59861235e-05  1.27512636e-03
  -1.94700217e-04  1.65693542e-03 -2.42366712e-03  3.57817944e-05
  -1.51123153e-03  4.15827639e-06 -1.06733834e-04  5.71480773e-06
   8.96949663e-02  1.33248781e-03  5.38059619e-05  5.19090103e-05
   2.23091137e-04  2.96750243e-05 -1.55684349e-05  4.34173912e-05]
 [-3.47241474e-03  2.34064041e-05  1.59861235e-05 -1.27512636e-03
   1.94700217e-04 -1.65693542e-03  2.42366712e-03 -3.57817944e-05
   1.51123153e-03 -4.15827639e-06  1.06733834e-04 -5.71480773e-06
  -8.96949663e-02 -1.33248781e-03 -5.38059619e-05 -5.19090103e-05
  -2.23091137e-04 -2.96750243e-05  1.55684349e-05 -4.34173912e-05]]
[[ 1.61204237e-05 -4.00393011e-06 -4.69536862e-03 -8.04528807e-06
   1.00880832e-04  1.50001390e-04 -1.08095998e-05 -1.61597284e-04
   9.91643485e-05  3.64421034e-02  5.01043590e-05 -9.32888908e-04
  -5.17722568e-05  2.61507560e-03 -3.09397578e-02 -8.07634607e-06
   1.47811281e-03  1.71302815e-04 -3.

  -3.65840601e-05  7.76249150e-06]]
[[ 3.47241395e-03 -2.34064084e-05 -1.59861273e-05  1.27512629e-03
  -1.94700171e-04  1.65693579e-03 -2.42366726e-03  3.57817849e-05
  -1.51123147e-03  4.15827652e-06 -1.06733830e-04  5.71480484e-06
   8.96949592e-02  1.33248765e-03  5.38059552e-05  5.19090114e-05
   2.23091110e-04  2.96750305e-05 -1.55684213e-05  4.34173943e-05]
 [-3.47241395e-03  2.34064084e-05  1.59861273e-05 -1.27512629e-03
   1.94700171e-04 -1.65693579e-03  2.42366726e-03 -3.57817849e-05
   1.51123147e-03 -4.15827652e-06  1.06733830e-04 -5.71480484e-06
  -8.96949592e-02 -1.33248765e-03 -5.38059552e-05 -5.19090114e-05
  -2.23091110e-04 -2.96750305e-05  1.55684213e-05 -4.34173943e-05]]
[[ 1.61204272e-05 -4.00393179e-06 -4.69536523e-03 -8.04528627e-06
   1.00880834e-04  1.50001307e-04 -1.08095988e-05 -1.61597266e-04
   9.91643447e-05  3.64421188e-02  5.01043240e-05 -9.32888802e-04
  -5.17722545e-05  2.61507660e-03 -3.09397520e-02 -8.07634217e-06
   1.47811356e-03  1.71302790e-04 -3.

  -3.65840597e-05  7.76249650e-06]]
[[ 3.47241430e-03 -2.34064099e-05 -1.59861279e-05  1.27512643e-03
  -1.94700189e-04  1.65693597e-03 -2.42366751e-03  3.57817874e-05
  -1.51123165e-03  4.15827691e-06 -1.06733841e-04  5.71480538e-06
   8.96949682e-02  1.33248782e-03  5.38059609e-05  5.19090175e-05
   2.23091134e-04  2.96750331e-05 -1.55684227e-05  4.34173982e-05]
 [-3.47241430e-03  2.34064099e-05  1.59861279e-05 -1.27512643e-03
   1.94700189e-04 -1.65693597e-03  2.42366751e-03 -3.57817874e-05
   1.51123165e-03 -4.15827691e-06  1.06733841e-04 -5.71480538e-06
  -8.96949682e-02 -1.33248782e-03 -5.38059609e-05 -5.19090175e-05
  -2.23091134e-04 -2.96750331e-05  1.55684227e-05 -4.34173982e-05]]
[[ 1.61204272e-05 -4.00393179e-06 -4.69536523e-03 -8.04528858e-06
   1.00880834e-04  1.50001307e-04 -1.08095992e-05 -1.61597314e-04
   9.91643447e-05  3.64421188e-02  5.01043700e-05 -9.32888802e-04
  -5.17722636e-05  2.61507660e-03 -3.09397592e-02 -8.07634217e-06
   1.47811356e-03  1.71302817e-04 -3.

  -3.65840598e-05  7.76249518e-06]]
[[ 3.47241407e-03 -2.34064096e-05 -1.59861275e-05  1.27512635e-03
  -1.94700177e-04  1.65693592e-03 -2.42366740e-03  3.57817868e-05
  -1.51123159e-03  4.15827679e-06 -1.06733838e-04  5.71480541e-06
   8.96949633e-02  1.33248781e-03  5.38059564e-05  5.19090172e-05
   2.23091119e-04  2.96750321e-05 -1.55684212e-05  4.34173961e-05]
 [-3.47241407e-03  2.34064096e-05  1.59861275e-05 -1.27512635e-03
   1.94700177e-04 -1.65693592e-03  2.42366740e-03 -3.57817868e-05
   1.51123159e-03 -4.15827679e-06  1.06733838e-04 -5.71480541e-06
  -8.96949633e-02 -1.33248781e-03 -5.38059564e-05 -5.19090172e-05
  -2.23091119e-04 -2.96750321e-05  1.55684212e-05 -4.34173961e-05]]
[[ 1.61204322e-05 -4.00393259e-06 -4.69536265e-03 -8.04528807e-06
   1.00880842e-04  1.50001299e-04 -1.08095998e-05 -1.61597284e-04
   9.91643411e-05  3.64421303e-02  5.01043590e-05 -9.32888652e-04
  -5.17722568e-05  2.61507935e-03 -3.09397578e-02 -8.07634289e-06
   1.47811517e-03  1.71302815e-04 -3.

  -3.65844559e-05  7.76250234e-06]]
[[ 3.47241496e-03 -2.34064141e-05 -1.59861301e-05  1.27512670e-03
  -1.94700224e-04  1.65693632e-03 -2.42366800e-03  3.57817940e-05
  -1.51123198e-03  4.15827775e-06 -1.06733863e-04  5.71480661e-06
   8.96949859e-02  1.33248812e-03  5.38059711e-05  5.19090294e-05
   2.23091179e-04  2.96750393e-05 -1.55684255e-05  4.34174065e-05]
 [-3.47241496e-03  2.34064141e-05  1.59861301e-05 -1.27512670e-03
   1.94700224e-04 -1.65693632e-03  2.42366800e-03 -3.57817940e-05
   1.51123198e-03 -4.15827775e-06  1.06733863e-04 -5.71480661e-06
  -8.96949859e-02 -1.33248812e-03 -5.38059711e-05 -5.19090294e-05
  -2.23091179e-04 -2.96750393e-05  1.55684255e-05 -4.34174065e-05]]
[[ 1.61204272e-05 -4.00393179e-06 -4.69536523e-03 -8.04528810e-06
   1.00880834e-04  1.50001307e-04 -1.08096008e-05 -1.61597273e-04
   9.91643447e-05  3.64421188e-02  5.01043753e-05 -9.32888802e-04
  -5.17722459e-05  2.61507660e-03 -3.09397566e-02 -8.07634217e-06
   1.47811356e-03  1.71302834e-04 -3.

# Batchnorm for deep networks
Run the following to train a six-layer network on a subset of 1000 training examples both with and without batch normalization.

In [9]:
np.random.seed(231)
# Try training a very deep net with batchnorm
hidden_dims = [100, 100, 100, 100, 100]

num_train = 1000
small_data = {
  'X_train': data['X_train'][:num_train],
  'y_train': data['y_train'][:num_train],
  'X_val': data['X_val'],
  'y_val': data['y_val'],
}

weight_scale = 2e-2
bn_model = FullyConnectedNet(hidden_dims, weight_scale=weight_scale, normalization='batchnorm')
model = FullyConnectedNet(hidden_dims, weight_scale=weight_scale, normalization=None)

print('Solver with batch norm:')
bn_solver = Solver(bn_model, small_data,
                num_epochs=10, batch_size=50,
                update_rule='adam',
                optim_config={
                  'learning_rate': 1e-3,
                },
                verbose=True,print_every=20)
bn_solver.train()

print('\nSolver without batch norm:')
solver = Solver(model, small_data,
                num_epochs=10, batch_size=50,
                update_rule='adam',
                optim_config={
                  'learning_rate': 1e-3,
                },
                verbose=True, print_every=20)
solver.train()

Solver with batch norm:


KeyError: 'gamma6'

Run the following to visualize the results from two networks trained above. You should find that using batch normalization helps the network to converge much faster.

In [ ]:
def plot_training_history(title, label, baseline, bn_solvers, plot_fn, bl_marker='.', bn_marker='.', labels=None):
    """utility function for plotting training history"""
    plt.title(title)
    plt.xlabel(label)
    bn_plots = [plot_fn(bn_solver) for bn_solver in bn_solvers]
    bl_plot = plot_fn(baseline)
    num_bn = len(bn_plots)
    for i in range(num_bn):
        label='with_norm'
        if labels is not None:
            label += str(labels[i])
        plt.plot(bn_plots[i], bn_marker, label=label)
    label='baseline'
    if labels is not None:
        label += str(labels[0])
    plt.plot(bl_plot, bl_marker, label=label)
    plt.legend(loc='lower center', ncol=num_bn+1) 

    
plt.subplot(3, 1, 1)
plot_training_history('Training loss','Iteration', solver, [bn_solver], \
                      lambda x: x.loss_history, bl_marker='o', bn_marker='o')
plt.subplot(3, 1, 2)
plot_training_history('Training accuracy','Epoch', solver, [bn_solver], \
                      lambda x: x.train_acc_history, bl_marker='-o', bn_marker='-o')
plt.subplot(3, 1, 3)
plot_training_history('Validation accuracy','Epoch', solver, [bn_solver], \
                      lambda x: x.val_acc_history, bl_marker='-o', bn_marker='-o')

plt.gcf().set_size_inches(15, 15)
plt.show()

# Batch normalization and initialization
We will now run a small experiment to study the interaction of batch normalization and weight initialization.

The first cell will train 8-layer networks both with and without batch normalization using different scales for weight initialization. The second layer will plot training accuracy, validation set accuracy, and training loss as a function of the weight initialization scale.

In [ ]:
np.random.seed(231)
# Try training a very deep net with batchnorm
hidden_dims = [50, 50, 50, 50, 50, 50, 50]
num_train = 1000
small_data = {
  'X_train': data['X_train'][:num_train],
  'y_train': data['y_train'][:num_train],
  'X_val': data['X_val'],
  'y_val': data['y_val'],
}

bn_solvers_ws = {}
solvers_ws = {}
weight_scales = np.logspace(-4, 0, num=20)
for i, weight_scale in enumerate(weight_scales):
  print('Running weight scale %d / %d' % (i + 1, len(weight_scales)))
  bn_model = FullyConnectedNet(hidden_dims, weight_scale=weight_scale, normalization='batchnorm')
  model = FullyConnectedNet(hidden_dims, weight_scale=weight_scale, normalization=None)

  bn_solver = Solver(bn_model, small_data,
                  num_epochs=10, batch_size=50,
                  update_rule='adam',
                  optim_config={
                    'learning_rate': 1e-3,
                  },
                  verbose=False, print_every=200)
  bn_solver.train()
  bn_solvers_ws[weight_scale] = bn_solver

  solver = Solver(model, small_data,
                  num_epochs=10, batch_size=50,
                  update_rule='adam',
                  optim_config={
                    'learning_rate': 1e-3,
                  },
                  verbose=False, print_every=200)
  solver.train()
  solvers_ws[weight_scale] = solver

In [ ]:
# Plot results of weight scale experiment
best_train_accs, bn_best_train_accs = [], []
best_val_accs, bn_best_val_accs = [], []
final_train_loss, bn_final_train_loss = [], []

for ws in weight_scales:
  best_train_accs.append(max(solvers_ws[ws].train_acc_history))
  bn_best_train_accs.append(max(bn_solvers_ws[ws].train_acc_history))
  
  best_val_accs.append(max(solvers_ws[ws].val_acc_history))
  bn_best_val_accs.append(max(bn_solvers_ws[ws].val_acc_history))
  
  final_train_loss.append(np.mean(solvers_ws[ws].loss_history[-100:]))
  bn_final_train_loss.append(np.mean(bn_solvers_ws[ws].loss_history[-100:]))
  
plt.subplot(3, 1, 1)
plt.title('Best val accuracy vs weight initialization scale')
plt.xlabel('Weight initialization scale')
plt.ylabel('Best val accuracy')
plt.semilogx(weight_scales, best_val_accs, '-o', label='baseline')
plt.semilogx(weight_scales, bn_best_val_accs, '-o', label='batchnorm')
plt.legend(ncol=2, loc='lower right')

plt.subplot(3, 1, 2)
plt.title('Best train accuracy vs weight initialization scale')
plt.xlabel('Weight initialization scale')
plt.ylabel('Best training accuracy')
plt.semilogx(weight_scales, best_train_accs, '-o', label='baseline')
plt.semilogx(weight_scales, bn_best_train_accs, '-o', label='batchnorm')
plt.legend()

plt.subplot(3, 1, 3)
plt.title('Final training loss vs weight initialization scale')
plt.xlabel('Weight initialization scale')
plt.ylabel('Final training loss')
plt.semilogx(weight_scales, final_train_loss, '-o', label='baseline')
plt.semilogx(weight_scales, bn_final_train_loss, '-o', label='batchnorm')
plt.legend()
plt.gca().set_ylim(1.0, 3.5)

plt.gcf().set_size_inches(15, 15)
plt.show()

## Inline Question 1:
Describe the results of this experiment. How does the scale of weight initialization affect models with/without batch normalization differently, and why?

## Answer:
[FILL THIS IN]


# Batch normalization and batch size
We will now run a small experiment to study the interaction of batch normalization and batch size.

The first cell will train 6-layer networks both with and without batch normalization using different batch sizes. The second layer will plot training accuracy and validation set accuracy over time.

In [ ]:
def run_batchsize_experiments(normalization_mode):
    np.random.seed(231)
    # Try training a very deep net with batchnorm
    hidden_dims = [100, 100, 100, 100, 100]
    num_train = 1000
    small_data = {
      'X_train': data['X_train'][:num_train],
      'y_train': data['y_train'][:num_train],
      'X_val': data['X_val'],
      'y_val': data['y_val'],
    }
    n_epochs=10
    weight_scale = 2e-2
    batch_sizes = [5,10,50]
    lr = 10**(-3.5)
    solver_bsize = batch_sizes[0]

    print('No normalization: batch size = ',solver_bsize)
    model = FullyConnectedNet(hidden_dims, weight_scale=weight_scale, normalization=None)
    solver = Solver(model, small_data,
                    num_epochs=n_epochs, batch_size=solver_bsize,
                    update_rule='adam',
                    optim_config={
                      'learning_rate': lr,
                    },
                    verbose=False)
    solver.train()
    
    bn_solvers = []
    for i in range(len(batch_sizes)):
        b_size=batch_sizes[i]
        print('Normalization: batch size = ',b_size)
        bn_model = FullyConnectedNet(hidden_dims, weight_scale=weight_scale, normalization=normalization_mode)
        bn_solver = Solver(bn_model, small_data,
                        num_epochs=n_epochs, batch_size=b_size,
                        update_rule='adam',
                        optim_config={
                          'learning_rate': lr,
                        },
                        verbose=False)
        bn_solver.train()
        bn_solvers.append(bn_solver)
        
    return bn_solvers, solver, batch_sizes

batch_sizes = [5,10,50]
bn_solvers_bsize, solver_bsize, batch_sizes = run_batchsize_experiments('batchnorm')

In [ ]:
plt.subplot(2, 1, 1)
plot_training_history('Training accuracy (Batch Normalization)','Epoch', solver_bsize, bn_solvers_bsize, \
                      lambda x: x.train_acc_history, bl_marker='-^', bn_marker='-o', labels=batch_sizes)
plt.subplot(2, 1, 2)
plot_training_history('Validation accuracy (Batch Normalization)','Epoch', solver_bsize, bn_solvers_bsize, \
                      lambda x: x.val_acc_history, bl_marker='-^', bn_marker='-o', labels=batch_sizes)

plt.gcf().set_size_inches(15, 10)
plt.show()

## Inline Question 2:
Describe the results of this experiment. What does this imply about the relationship between batch normalization and batch size? Why is this relationship observed?

## Answer:
[FILL THIS IN]


# Layer Normalization
Batch normalization has proved to be effective in making networks easier to train, but the dependency on batch size makes it less useful in complex networks which have a cap on the input batch size due to hardware limitations. 

Several alternatives to batch normalization have been proposed to mitigate this problem; one such technique is Layer Normalization [2]. Instead of normalizing over the batch, we normalize over the features. In other words, when using Layer Normalization, each feature vector corresponding to a single datapoint is normalized based on the sum of all terms within that feature vector.

[2] [Ba, Jimmy Lei, Jamie Ryan Kiros, and Geoffrey E. Hinton. "Layer Normalization." stat 1050 (2016): 21.](https://arxiv.org/pdf/1607.06450.pdf)

## Inline Question 3:
Which of these data preprocessing steps is analogous to batch normalization, and which is analogous to layer normalization?

1. Scaling each image in the dataset, so that the RGB channels for each row of pixels within an image sums up to 1.
2. Scaling each image in the dataset, so that the RGB channels for all pixels within an image sums up to 1.  
3. Subtracting the mean image of the dataset from each image in the dataset.
4. Setting all RGB values to either 0 or 1 depending on a given threshold.

## Answer:
[FILL THIS IN]


# Layer Normalization: Implementation

Now you'll implement layer normalization. This step should be relatively straightforward, as conceptually the implementation is almost identical to that of batch normalization. One significant difference though is that for layer normalization, we do not keep track of the moving moments, and the testing phase is identical to the training phase, where the mean and variance are directly calculated per datapoint.

Here's what you need to do:

* In `cs231n/layers.py`, implement the forward pass for layer normalization in the function `layernorm_backward`. 

Run the cell below to check your results.
* In `cs231n/layers.py`, implement the backward pass for layer normalization in the function `layernorm_backward`. 

Run the second cell below to check your results.
* Modify `cs231n/classifiers/fc_net.py` to add layer normalization to the `FullyConnectedNet`. When the `normalization` flag is set to `"layernorm"` in the constructor, you should insert a layer normalization layer before each ReLU nonlinearity. 

Run the third cell below to run the batch size experiment on layer normalization.

In [ ]:
# Check the training-time forward pass by checking means and variances
# of features both before and after layer normalization   

# Simulate the forward pass for a two-layer network
np.random.seed(231)
N, D1, D2, D3 =4, 50, 60, 3
X = np.random.randn(N, D1)
W1 = np.random.randn(D1, D2)
W2 = np.random.randn(D2, D3)
a = np.maximum(0, X.dot(W1)).dot(W2)

print('Before layer normalization:')
print_mean_std(a,axis=1)

gamma = np.ones(D3)
beta = np.zeros(D3)
# Means should be close to zero and stds close to one
print('After layer normalization (gamma=1, beta=0)')
a_norm, _ = layernorm_forward(a, gamma, beta, {'mode': 'train'})
print_mean_std(a_norm,axis=1)

gamma = np.asarray([3.0,3.0,3.0])
beta = np.asarray([5.0,5.0,5.0])
# Now means should be close to beta and stds close to gamma
print('After layer normalization (gamma=', gamma, ', beta=', beta, ')')
a_norm, _ = layernorm_forward(a, gamma, beta, {'mode': 'train'})
print_mean_std(a_norm,axis=1)

In [ ]:
# Gradient check batchnorm backward pass
np.random.seed(231)
N, D = 4, 5
x = 5 * np.random.randn(N, D) + 12
gamma = np.random.randn(D)
beta = np.random.randn(D)
dout = np.random.randn(N, D)

ln_param = {}
fx = lambda x: layernorm_forward(x, gamma, beta, ln_param)[0]
fg = lambda a: layernorm_forward(x, a, beta, ln_param)[0]
fb = lambda b: layernorm_forward(x, gamma, b, ln_param)[0]

dx_num = eval_numerical_gradient_array(fx, x, dout)
da_num = eval_numerical_gradient_array(fg, gamma.copy(), dout)
db_num = eval_numerical_gradient_array(fb, beta.copy(), dout)

_, cache = layernorm_forward(x, gamma, beta, ln_param)
dx, dgamma, dbeta = layernorm_backward(dout, cache)

#You should expect to see relative errors between 1e-12 and 1e-8
print('dx error: ', rel_error(dx_num, dx))
print('dgamma error: ', rel_error(da_num, dgamma))
print('dbeta error: ', rel_error(db_num, dbeta))

# Layer Normalization and batch size

We will now run the previous batch size experiment with layer normalization instead of batch normalization. Compared to the previous experiment, you should see a markedly smaller influence of batch size on the training history!

In [ ]:
ln_solvers_bsize, solver_bsize, batch_sizes = run_batchsize_experiments('layernorm')

plt.subplot(2, 1, 1)
plot_training_history('Training accuracy (Layer Normalization)','Epoch', solver_bsize, ln_solvers_bsize, \
                      lambda x: x.train_acc_history, bl_marker='-^', bn_marker='-o', labels=batch_sizes)
plt.subplot(2, 1, 2)
plot_training_history('Validation accuracy (Layer Normalization)','Epoch', solver_bsize, ln_solvers_bsize, \
                      lambda x: x.val_acc_history, bl_marker='-^', bn_marker='-o', labels=batch_sizes)

plt.gcf().set_size_inches(15, 10)
plt.show()

## Inline Question 4:
When is layer normalization likely to not work well, and why?

1. Using it in a very deep network
2. Having a very small dimension of features
3. Having a high regularization term


## Answer:
[FILL THIS IN]
